In [2]:
import pandas as pd
import numpy as np
import pickle

In [3]:
import os
os.listdir("../../Data/data")

['PageTimes-2022-12-30.csv',
 'improv_ctrl_2022-12-30.csv',
 'improv_focus_2023-01-06.csv',
 'PageTimes-2023-01-06.csv']

In [6]:
ctrl = pd.read_csv('../../Data/data/improv_ctrl_2022-12-30.csv')
ctrl = ctrl[ctrl['participant.label'].notna()]
ctrl_1 = ctrl[ctrl["player.id_in_group"] == 1]

In [7]:
focus = pd.read_csv('../../Data/data/improv_focus_2023-01-06.csv')
focus = focus[focus['participant.label'].notna()]
focus_1 = focus[focus["player.id_in_group"] == 1]

In [32]:
ctrl_1['participant.id_in_session']

0         1
1         2
2         3
4         5
5         6
         ..
17758    59
17759    60
17760    61
17761    62
17762    63
Name: participant.id_in_session, Length: 1920, dtype: int64

In [8]:
def filter_df_by_story(df, storynum, version='ctrl'):
    if storynum == 1:
        df = df[df["subsession.round_number"] <= 12]
    elif storynum == 2:
        df = df[(df["subsession.round_number"] > 12) & (df["subsession.round_number"] <= 30)]
    elif storynum == 3:
        if version == 'ctrl':
            df = df[(df["subsession.round_number"] > 30) & (df["subsession.round_number"] <= 42)]
        else:
            df = df[(df["subsession.round_number"] > 37) & (df["subsession.round_number"] <= 49)]
    elif storynum ==4:
        if version == 'ctrl':
            df = df[(df["subsession.round_number"] > 42) & (df["subsession.round_number"] <= 60)]
        else:
            df = df[(df["subsession.round_number"] > 49) & (df["subsession.round_number"] <= 67)]
    return df
    

In [22]:
def get_story_script(df, label, storynum=1, mode="ind", version="ctrl"):
   
    df = filter_df_by_story(df, storynum, version)
    player1_lines = df[df["participant.label"] == label]["group.playerA_line"].to_list()
    player2_lines = df[df["participant.label"] == label]["group.playerB_line"].to_list()
    script = ""
    start = 0
    if (storynum > 2) and (version == "focus"):
        start = 1
    for i in range(len(player1_lines)):
        if i % 2 == start:
            
            player_line = player1_lines[i]
            if not pd.isnull(player_line):
                player_line = player_line.replace("\"", "\\\"")
                script += "<font color='blue'>PlayerA: </font> %s <br/>" % player_line
                #script +=  player_line + ".# "
        else:
            player_line = player2_lines[i]
            if not pd.isnull(player_line):
                player_line = player_line.replace("\"", "\\\"")
                script += "<font color='green'>PlayerB: </font> %s <br/>" % player_line
                #script +=  player_line + ".$ "
            
    return script

In [21]:
string = "String, \"Yes, there\""
string = string.replace("\"", "\\\"")
print(string)

String, \"Yes, there\"


In [25]:
subject_list = ctrl_1["participant.label"].unique()

for subject_id in subject_list:
    print("dict(name = '%s'," % subject_id)
    script = get_story_script(ctrl, label=subject_id, storynum=4, mode="ind", version="ctrl")
    print("story=\"%s\")," % script)

dict(name = '6165e0b51a883e9db8cc7146',
story="<font color='blue'>PlayerA: </font> I couldn't imagine that the robbery would turn into a murder. The crime scene was awful!! <br/><font color='green'>PlayerB: </font> There were no jewels recorded to be stolen too, which was interesting but very suspect.  <br/><font color='blue'>PlayerA: </font> We were lucky because we could get clear footprints outside the store <br/><font color='green'>PlayerB: </font> The owner of the store let out a scream as he saw his employee dead on the floor, but didn't seem surprised. <br/><font color='blue'>PlayerA: </font> Next to the victim was a knife. He was killed by  <br/><font color='green'>PlayerB: </font> The knife looked strangely familiar, as if I had already seen it before. I asked for CCTV images. <br/><font color='blue'>PlayerA: </font> It was interesting the fact that the murderer was a woman! The  <br/><font color='green'>PlayerB: </font> She had used a clever disguise as an old lady despite he

In [29]:
subject_list = focus_1["participant.label"].unique()

for subject_id in subject_list:
    print("dict(name = '%s'," % subject_id)
    script = get_story_script(focus, label=subject_id, storynum=4, mode="ind", version="focus")
    print("story=\"%s\")," % script)

dict(name = '5e8eeb7b9422bb1a1eda54a2',
story="<font color='green'>PlayerB: </font> A young girl had murder with a knife her mother . She was clever and <br/><font color='blue'>PlayerA: </font> interesting. There was an expectation that s <br/><font color='green'>PlayerB: </font> footprints where there on the crime scene but they werent any . It was clea <br/><font color='blue'>PlayerA: </font> It was interesting if the girl had even comitted the crime.  <br/><font color='green'>PlayerB: </font> Some jewels where missing aslo and the car was stolen . Was it something else in di <br/><font color='blue'>PlayerA: </font> The crime was clever. There was an expectation on me to figure out what really happened. Where were the  <br/><font color='green'>PlayerB: </font> suspects interrogated i had to double check that  <br/><font color='blue'>PlayerA: </font> There were no reports of the suspects being questioned. They we <br/><font color='green'>PlayerB: </font> tried to enjoy dinner with col

In [30]:
a = [1,2,3,4]
a[:2]

[1, 2]

In [20]:
def get_prefixes_story(storynum):
    if storynum == 1:
        prefix = "It was my first day on the job as an assistant zookeeper when the animals got loose. It was also all my fault."
    elif storynum == 2:
        prefix = "It was the first day of school and I was already feeling out of place."
    elif storynum == 3:
        prefix = "Late for work, I throw open the front door and find myself face-to-face with a UPS driver standing next to the biggest box I’ve ever seen."
    elif storynum == 4:
        prefix = "My first case as a detective, and I did not expect it to be this hard."
    return prefix

In [53]:
def get_prefix_suffix_pairs(df, label, storynum=1, version='ctrl'):
    df = filter_df_by_story(df, storynum, version=version)
    prefix_suffix = []
    
    prefix = get_prefixes_story(storynum)
    player1_lines = df[df["participant.label"] == label]["group.playerA_line"].to_list()
    player2_lines = df[df["participant.label"] == label]["group.playerB_line"].to_list()
    player1_lines_fna = []
    player2_lines_fna = []
    
    start = 0
    if (storynum > 2) and (version == "focus"):
        start = 1
        
    for i in range(12):
        if i % 2 == start:
            player_line = player1_lines[i]
            if not pd.isnull(player_line):
                prefix_suffix.append([prefix, player_line])
                prefix = player_line
        else:
            player_line = player2_lines[i]
            if not pd.isnull(player_line):
                prefix_suffix.append([prefix, player_line])
                prefix = player_line
    return prefix_suffix

In [63]:
prefix_suffix_pairs = {}
subject_list = ctrl_1["participant.label"].unique()
for subject in subject_list:
    prefix_suffix_pairs[subject] = {}
    for storynum in range(1, 5):
        pairs = get_prefix_suffix_pairs(ctrl_1, label=subject, storynum=storynum, version="focus")
        prefix_suffix_pairs[subject][storynum] = pairs 
        

In [64]:
pickle.dump(prefix_suffix_pairs, open("prefixes_focus.pkl", "wb"))

In [32]:
def get_prefix_suffix_pairs_player(df, label, storynum=1, player=1, version="ctrl"):
    df = filter_df_by_story(df, storynum, version=version)
    prefixes = []
    suffixes = []
    prefix = get_prefixes_story(storynum)
    player1_lines = df[df["participant.label"] == label]["group.playerA_line"].to_list()
    player2_lines = df[df["participant.label"] == label]["group.playerB_line"].to_list()
    for i in range(12):
        if i % 2 == 0:
            print(player1_lines)
            player_line = player1_lines[i]
            if not pd.isnull(player_line):
                if player == 1:
                    prefixes.append(prefix)
                    suffixes.append(player_line)
                prefix = player_line
        else:
            player_line = player2_lines[i]
            if not pd.isnull(player_line):
                if player == 2:
                    prefixes.append(prefix)
                    suffixes.append(player_line)
                prefix = player_line
    return prefixes, suffixes

In [34]:
p, s = get_prefix_suffix_pairs_player(ctrl_1, label="5e8eeb7b9422bb1a1eda54a2", version="focus")

["I was nervous on my first day and didn't receive proper training. I'm annoyed at myself for letting this happen.", nan, "I didn't know what to do and needed to deal with it quickly, before someone noticed  ", nan, 'i told him i ', nan, 'disbelief and felt alarmed. ', nan, 'i then started to think about how i could get the elephants back into their room', nan, 'I then would have to release another animal out. "No," I thought to myself, "That wouldn\'t be a good idea"', nan]
["I was nervous on my first day and didn't receive proper training. I'm annoyed at myself for letting this happen.", nan, "I didn't know what to do and needed to deal with it quickly, before someone noticed  ", nan, 'i told him i ', nan, 'disbelief and felt alarmed. ', nan, 'i then started to think about how i could get the elephants back into their room', nan, 'I then would have to release another animal out. "No," I thought to myself, "That wouldn\'t be a good idea"', nan]
["I was nervous on my first day and didn

In [51]:
get_prefix_suffix_pairs(ctrl_1, label="5e8eeb7b9422bb1a1eda54a2", storynum=4, version="focus")

[['My first case as a detective, and I did not expect it to be this hard.',
  'A young girl had murder with a knife her mother . She was clever and'],
 ['A young girl had murder with a knife her mother . She was clever and',
  'interesting. There was an expectation that s'],
 ['interesting. There was an expectation that s',
  'footprints where there on the crime scene but they werent any . It was clea'],
 ['footprints where there on the crime scene but they werent any . It was clea',
  'It was interesting if the girl had even comitted the crime. '],
 ['It was interesting if the girl had even comitted the crime. ',
  'Some jewels where missing aslo and the car was stolen . Was it something else in di'],
 ['Some jewels where missing aslo and the car was stolen . Was it something else in di',
  'The crime was clever. There was an expectation on me to figure out what really happened. Where were the '],
 ['The crime was clever. There was an expectation on me to figure out what really happen

In [41]:
df = filter_df_by_story(ctrl_1, storynum=3, version="focus")

In [42]:
df

participant.id_in_session participant.code         participant.label  \
9388                           5         dyyxyp6l  5e8eeb7b9422bb1a1eda54a2   
9389                           6         4ldljmjh  615e28098f24bcb3e5e83300   
9390                           7         xrvgfpmb  612d5ca50be0e9ff3505561f   
9391                           8         dd3zhcdj  607c8d109c2c960d3430abec   
9392                           9         zrco80st  855A1jC08lN7I9mv7064963S   
...                          ...              ...                       ...   
12194                         61         kmevbee1  604ff1c798e159aa44a2e912   
12195                         62         m6s4571u  61314fbda0ad57bb6d9d32b3   
12196                         63         jv7h9r64  572bc38f34b25a0010dbe9c4   
12198                         65         x4y4wkhw  5e999ce87c90241d0009d8c5   
12199                         66         so3k46o9  5fd5038ab78cf82f89c86bdc   

       participant._is_bot  participant._index_in_pages  \
9388                     0                         2144   
9389                     0                         2144   
9390                     0                         2144   
9391                     0                         2144   
9392                     0                            1   
...                    ...                          ...   
12194                    0                         2144   
12195                    0                         2144   
12196                    0                         2144   
12198                    0                         2144   
12199                    0                         2144   

       participant._max_page_index participant._current_app_name  \
9388                          2144                  improv_focus   
9389                          2144                  improv_focus   
9390                          2144                  improv_focus   
9391                          2144                  improv_focus   
9392                          2144                  improv_focus   
...                            ...                           ...   
12194                         2144                  improv_focus   
12195                         2144                  improv_focus   
12196                         2144                  improv_focus   
12198                         2144                  improv_focus   
12199                         2144                  improv_focus   

      participant._current_page_name participant.time_started_utc  \
9388                         EndPage   2023-01-06 18:01:09.801803   
9389                         EndPage   2023-01-06 18:01:16.541253   
9390                         EndPage   2023-01-06 18:01:16.887384   
9391                         EndPage   2023-01-06 18:01:16.850870   
9392                         Consent   2023-01-06 18:01:19.128568   
...                              ...                          ...   
12194                        EndPage   2023-01-06 18:07:03.254333   
12195                        EndPage   2023-01-06 18:08:09.926663   
12196                        EndPage   2023-01-06 18:09:37.378887   
12198                        EndPage   2023-01-06 18:13:51.028181   
12199                        EndPage   2023-01-06 18:38:54.297145   

       participant.visited  ...  \
9388                     1  ...   
9389                     1  ...   
9390                     1  ...   
9391                     1  ...   
9392                     1  ...   
...                    ...  ...   
12194                    1  ...   
12195                    1  ...   
12196                    1  ...   
12198                    1  ...   
12199                    1  ...   

                                      group.playerA_line  \
9388                                                 NaN   
9389                                                 NaN   
9390                                                 NaN   
9391                                      

In [62]:
prefix_suffix_pairs

{'5e8eeb7b9422bb1a1eda54a2': {1: [['It was my first day on the job as an assistant zookeeper when the animals got loose. It was also all my fault.',
    "I was nervous on my first day and didn't receive proper training. I'm annoyed at myself for letting this happen."],
   ["I was nervous on my first day and didn't receive proper training. I'm annoyed at myself for letting this happen.",
    'The elephant sit all over the room '],
   ['The elephant sit all over the room ',
    "I didn't know what to do and needed to deal with it quickly, before someone noticed  "],
   ["I didn't know what to do and needed to deal with it quickly, before someone noticed  ",
    'the a kid come in the room and asked what was this mess on the floor'],
   ['the a kid come in the room and asked what was this mess on the floor',
    'i told him i '],
   ['i told him i ',
    'gave the elephant some laxatives and this was the results. He looked at me in '],
   ['gave the elephant some laxatives and this was th